# folium

In [37]:
import json
import urllib

import branca.colormap as cm
import folium
import pandas as pd
import numpy as np

from folium import plugins
from ipywidgets import interact

%matplotlib inline

# [Datos abiertos Santander](http://datos.santander.es/)

In [38]:
URL = 'http://datos.santander.es/api/rest/datasets/tusbic_estaciones.json'

In [39]:
# Obtención de datos
with urllib.request.urlopen(URL) as req:
    data = json.load(req)
    df = pd.DataFrame(data['resources'])
df.head()

ayto:direccion ayto:latitud  \
0                                      Severo Ochoa      43.4528   
1    Parque las Llamas (Aprox. Palacio de Deportes)      43.4757   
2  Calle de San Fernando (Aprox. Paseo del Alameda)      43.4607   
3             Calle Alta (Aprox. Mercado de México)       43.458   
4                                         Rucandial      43.4548   

  ayto:longitud                ayto:nombre ayto:total_puestos dc:identifier  \
0      -3.87139           016_SEVERO OCHOA                 20            16   
1      -3.79806      003_PARQUE LAS LLAMAS                 20             3   
2      -3.81798  013_CALLE DE SAN FERNANDO                 25            13   
3       -3.8248             012_CALLE ALTA                 15            12   
4       -3.8669              017_RUCANDIAL                 20            17   

            dc:modified                                                uri  
0  2019-04-08T22:38:06Z  http://datos.santander.es/api/datos/tusbic_est...  
1  2019-04-08T22:37:19Z  http://datos.santander.es/api/datos/tusbic_est...  
2  2019-04-08T22:37:09Z  http://datos.santander.es/api/datos/tusbic_est...  
3  2019-04-08T22:36:43Z  http://datos.santander.es/api/datos/tusbic_est...  
4  2019-04-08T22:36:24Z  http://datos.santander.es/api/datos/tusbic_est...

In [40]:
mapa = folium.Map([43.47, -3.82],
                  zoom_start=13)
df[['ayto:latitud', 'ayto:longitud', 'ayto:total_puestos']] = df[[
    'ayto:latitud', 'ayto:longitud', 'ayto:total_puestos'
]].astype(float)

# mark each station as a point
for index, row in df.iterrows():
    folium.CircleMarker([row['ayto:latitud'], row['ayto:longitud']],
                        radius=row['ayto:total_puestos'],
                        popup=row['ayto:nombre'],
                        fill_color="#3db7e4", # divvy color
                       ).add_to(mapa)

bicitus = df[['ayto:latitud', 'ayto:longitud', 'ayto:total_puestos']].values / [1, 1, 15]

mapa.add_child(plugins.HeatMap(bicitus, radius=40))
mapa

In [41]:
mapa = folium.Map([43.47, -3.82],
                  zoom_start=13,
                  tiles = 'stamentoner',
                  control_scale=True)

df[['ayto:latitud', 'ayto:longitud', 'ayto:total_puestos']] = df[[
    'ayto:latitud', 'ayto:longitud', 'ayto:total_puestos'
]].astype(float)

bicitus = df[['ayto:latitud', 'ayto:longitud', 'ayto:total_puestos']].values / [1, 1, 15]

mapa.add_child(plugins.HeatMap(bicitus, radius=40))
mapa

# [AEMET Open Data](http://www.aemet.es/en/datos_abiertos/AEMET_OpenData)

In [42]:
with open('estaciones.json', encoding='latin-1') as f:
    datos = json.load(f)
    estaciones = pd.DataFrame(datos)

def dms2dec(dms_str):
    degree = dms_str[:2]
    minute = dms_str[2:4]
    second = dms_str[4:6]
    sign = -1 if dms_str[-1] in 'swSW' else 1
    return sign * (int(degree) + float(minute) / 60 + float(second) / 3600)

estaciones[['latitud', 'longitud']] = estaciones[['latitud', 'longitud']].applymap(dms2dec)
estaciones.altitud = estaciones.altitud.astype(int)


In [43]:
mapa = folium.Map([40.47, -3.5], zoom_start=6)

for index, row in estaciones.iterrows():
    folium.map.Marker([row.latitud, row.longitud],
                        popup=f'{row.nombre}({row.indicativo})',
                       ).add_to(mapa)

valores = estaciones[['latitud', 'longitud', 'altitud']].values / [1, 1, estaciones.altitud.mean()]
mapa.add_child(plugins.HeatMap(valores))

mapa

# [INE](http://www.ine.es)

In [44]:
provincias = 'https://public.opendatasoft.com/explore/dataset/provincias-espanolas/download/?format=geojson'
# Obtención de datos
with urllib.request.urlopen(provincias) as req:
    geo_json_data = json.load(req)

In [45]:
tasa_paro = "http://www.ine.es/jaxiT3/files/t/es/csv_sc/9122.csv"
df = pd.read_csv(tasa_paro, 
                 sep=';', encoding='utf-8',
                 na_values='..',
                 header=[4, 5], index_col=0)

df.dropna(axis='rows', how='all', inplace=True)
df.dropna(axis='columns', how='all', inplace=True)

In [46]:
# Ordena los datos (gracias, INE)
estado = np.array(['Ocupados', 'Parados']).repeat(68)
df.columns = pd.MultiIndex.from_tuples(zip(estado, df.columns.get_level_values(1)))
df.index = df.index.map(lambda s: s.split()[0])
sexos = ['Ambos sexos', 'Hombres', 'Mujeres']

paro = [df[1 + 53 * i:53 + 53*i] for i in range(len(sexos))]
for i, item in enumerate(sexos):
    paro[i].set_index(
        pd.MultiIndex.from_tuples(zip(paro[i].index,
                                      np.repeat(item, len(paro[i]))),
                                  names=['provincia', 'sexo']),
        inplace=True
    )
# Genera la tasa de paro (%)
df = pd.concat(paro)
trimestres = df.columns.get_level_values(level=1).unique()

for trimestre in trimestres:
    df['Tasa', trimestre] = 100.0 * df['Parados', trimestre]/(df['Ocupados', trimestre] + df['Parados', trimestre])

## Ejemplo con una de las columnas

In [47]:
columna = df['Tasa', '2018T4'][:,'Ambos sexos']

In [48]:
def colores(feature, columna):
    return 'red' if columna[feature['properties']['codigo']] > columna.mean() else 'green'

step = cm.StepColormap(['green', 'yellow', 'red'],
                       vmin=columna.min(),
                       vmax=columna.max(),
                       caption='step')
linear_step = cm.LinearColormap(['green', 'yellow', 'red'],
                                vmin=columna.min(),
                                vmax=columna.max())

In [49]:
mapa = folium.Map([40.47, -3.5], zoom_start=6)

folium.GeoJson(
    geo_json_data,
    style_function=lambda feature: {
        'fillColor': colores(feature, columna),
#         'fillColor': step(columna[feature['properties']['codigo']]),
#         'fillColor': linear_step(columna[feature['properties']['codigo']]),
        'color' : 'black',
        'weight' : 2,
        'dashArray' : '5, 5',
        }
    ).add_to(mapa)
mapa

# mapa.add_child(step)
# mapa.add_child(linear_step)

## De forma alternativa, con `Choropleth`:

In [50]:
mapa = folium.Map([40.47, -3.5], zoom_start=6)

folium.Choropleth(
    geo_data=geo_json_data,
    data=df.Tasa['2018T1'][:, 'Ambos sexos'],
    key_on='feature.properties.codigo',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.8,
    nan_fill_color='purple',
    legend_name='Tasa de desempleo (%)',
    highlight=True
).add_to(mapa)

mapa

In [51]:
linear_step = cm.LinearColormap(['green', 'yellow', 'red'],
                               vmin=df.Tasa.quantile(.25).mean(),
                               vmax=df.Tasa.quantile(.75).mean())

step = cm.StepColormap(['green', 'yellow', 'red'],
                       vmin=df.Tasa.quantile(.25).mean(),
                       vmax=df.Tasa.quantile(.75).mean(),
                       caption='step')

def escala_media(valor):
    return 'red' if valor > columna.mean() else 'green'


def mapa_paro(trimestre='2018T4', sexo='Ambos sexos', escala='continua'):
    global columna
    columna = df['Tasa', trimestre][:, sexo]

    #####
    mapa = folium.Map([40.47, -3.5], zoom_start=6)
    if escala == 'continua':
        f_escala = linear_step
    elif escala == 'discreta':
        f_escala = step
    else:
        f_escala = escala_media
    folium.GeoJson(
        geo_json_data,
        style_function=lambda feature: {
            'fillColor': f_escala(columna[feature['properties']['codigo']]),
            'color' : 'black',
            'weight' : 2,
            'dashArray' : '5, 5',
            }
        ).add_to(mapa)
    if escala != 'media':
        mapa.add_child(f_escala)
    
    #####
    return mapa

interact(mapa_paro, trimestre=trimestres, sexo=sexos, escala=['continua', 'discreta', 'media']);

interactive(children=(Dropdown(description='trimestre', options=('2018T4', '2018T3', '2018T2', '2018T1', '2017…

## Mismo ejemplo simplificado, con `Choropleth`

In [52]:
def mapa_paro(trimestre='2018T4', sexo='Ambos sexos'):
    #####
    mapa = folium.Map([40.47, -3.5], zoom_start=6)
    folium.Choropleth(
        geo_data=geo_json_data,
        data=df.Tasa[trimestre][:, sexo],
        key_on='feature.properties.codigo',
        fill_color='YlOrRd',
        fill_opacity=0.7,
        line_opacity=0.8,
        nan_fill_color='purple',
        legend_name='Tasa de desempleo (%)',
        highlight=True
    ).add_to(mapa)
    #####
    return mapa

interact(mapa_paro, trimestre=trimestres, sexo=sexos);

interactive(children=(Dropdown(description='trimestre', options=('2018T4', '2018T3', '2018T2', '2018T1', '2017…